In [1]:
import pandas as pd
import numpy as np
import requests
import json
from pprint import pprint
from citipy import citipy

# Google API Key
from config import gkey

from sqlalchemy import create_engine

import pymysql
pymysql.install_as_MySQLdb()

### Store CSV into DataFrame: Vulture Migration Paths

In [2]:
excel_file = "Resources/Turkey vultures in North and South America - migration.xlsx"
vulture_data_df = pd.read_excel(excel_file, index_col=None)
vulture_data_df.head(2)

event-id  visible                timestamp  location-long  location-lat  \
0  283203879     True  2003-11-14 16:00:00.000      -75.39717      40.48933   
1  283203880     True  2003-11-14 17:00:00.000      -75.39717      40.48933   

   manually-marked-outlier sensor-type individual-taxon-canonical-name  \
0                    False         gps                  Cathartes aura   
1                    False         gps                  Cathartes aura   

   tag-local-identifier individual-local-identifier    ...     \
0                 42500                  Butterball    ...      
1                 42500                  Butterball    ...      

  animal-life-stage  animal-mass  attachment-type  \
0             adult       2372.0          harness   
1             adult       2372.0          harness   

                                 deployment-comments     deployment-id  \
0  trapped in Pennsylvania using padded-leg hold ...  42500-Butterball   
1  trapped in Pennsylvania using padded-leg hold ...  42500-Butterball   

       duty-cycle                   study-site tag-manufacturer-name tag-mass  \
0  1 fix per hour  East Coast of North America   Microwave Telemetry       70   
1  1 fix per hour  East Coast of North America   Microwave Telemetry       70   

  tag-model  
0    PTT100  
1    PTT100  

[2 rows x 32 columns]

In [3]:
vulture_data_df.columns

Index(['event-id', 'visible', 'timestamp', 'location-long', 'location-lat',
       'manually-marked-outlier', 'sensor-type',
       'individual-taxon-canonical-name', 'tag-local-identifier',
       'individual-local-identifier', 'study-name', 'utm-easting',
       'utm-northing', 'utm-zone', 'study-timezone', 'study-local-timestamp',
       'tag-id', 'animal-id', 'animal-taxon', 'deploy-on-date',
       'deploy-off-date', 'animal-comments', 'animal-life-stage',
       'animal-mass', 'attachment-type', 'deployment-comments',
       'deployment-id', 'duty-cycle', 'study-site', 'tag-manufacturer-name',
       'tag-mass', 'tag-model'],
      dtype='object')

In [4]:
vulture_data_df.keys()

Index(['event-id', 'visible', 'timestamp', 'location-long', 'location-lat',
       'manually-marked-outlier', 'sensor-type',
       'individual-taxon-canonical-name', 'tag-local-identifier',
       'individual-local-identifier', 'study-name', 'utm-easting',
       'utm-northing', 'utm-zone', 'study-timezone', 'study-local-timestamp',
       'tag-id', 'animal-id', 'animal-taxon', 'deploy-on-date',
       'deploy-off-date', 'animal-comments', 'animal-life-stage',
       'animal-mass', 'attachment-type', 'deployment-comments',
       'deployment-id', 'duty-cycle', 'study-site', 'tag-manufacturer-name',
       'tag-mass', 'tag-model'],
      dtype='object')

### Create new data with select columns

In [5]:
# Select columns 
new_vulture_data_df = vulture_data_df[['event-id', 'timestamp', 'location-long', 'location-lat','individual-taxon-canonical-name', 'tag-local-identifier',
       'individual-local-identifier']].copy()
new_vulture_data_df.head()

event-id                timestamp  location-long  location-lat  \
0  283203879  2003-11-14 16:00:00.000      -75.39717      40.48933   
1  283203880  2003-11-14 17:00:00.000      -75.39717      40.48933   
2  283203881  2003-11-14 18:00:00.000      -75.33317      40.32467   
3  283203882  2003-11-14 19:00:00.000      -75.35617      40.33983   
4  283203883  2003-11-14 20:00:00.000      -75.42650      40.31550   

  individual-taxon-canonical-name  tag-local-identifier  \
0                  Cathartes aura                 42500   
1                  Cathartes aura                 42500   
2                  Cathartes aura                 42500   
3                  Cathartes aura                 42500   
4                  Cathartes aura                 42500   

  individual-local-identifier  
0                  Butterball  
1                  Butterball  
2                  Butterball  
3                  Butterball  
4                  Butterball

### Clean DataFrame

In [6]:
new_vulture_data_df.count()

event-id                           220077
timestamp                          220077
location-long                      220077
location-lat                       220077
individual-taxon-canonical-name    220077
tag-local-identifier               220077
individual-local-identifier        220077
dtype: int64

In [7]:
# drop rows without long and lat
new_vulture_data_df = new_vulture_data_df.dropna(how="any")
new_vulture_data_df.count()

event-id                           220077
timestamp                          220077
location-long                      220077
location-lat                       220077
individual-taxon-canonical-name    220077
tag-local-identifier               220077
individual-local-identifier        220077
dtype: int64

In [8]:
# filter data to only keep turkey vulture (Cathartes aura) data
new_vulture_data_df = new_vulture_data_df.loc[new_vulture_data_df
                                              ["individual-taxon-canonical-name"] == "Cathartes aura", :]
new_vulture_data_df.count()

event-id                           220077
timestamp                          220077
location-long                      220077
location-lat                       220077
individual-taxon-canonical-name    220077
tag-local-identifier               220077
individual-local-identifier        220077
dtype: int64

In [9]:
new_vulture_data_df.dtypes

event-id                             int64
timestamp                           object
location-long                      float64
location-lat                       float64
individual-taxon-canonical-name     object
tag-local-identifier                 int64
individual-local-identifier         object
dtype: object

In [10]:
# check to prevent duplicate loading (inqury for database)

### Connect to local database

In [11]:
database_path = "vulture_etl"
engine = create_engine(f"sqlite:///{database_path}")

### Check for tables

In [12]:
engine.table_names()

[]

### Use pandas to load csv converted DataFrame into database

In [13]:
new_vulture_data_df.to_sql(name='migration_paths', con=engine, if_exists='append', index=False)

### Use pandas to import second csv: Vulture Info by name

In [14]:
csv_file = "Resources/Turkey vultures in North and South America-reference-data.csv"
vulture_info_df = pd.read_csv(csv_file, low_memory=False)
vulture_info_df.head()

tag-id   animal-id    animal-taxon           deploy-on-date  \
0   42500  Butterball  Cathartes aura  2003-11-14 16:00:00.000   
1   52067        Irma  Cathartes aura  2004-09-06 17:00:00.000   
2   42500  Schaumboch  Cathartes aura  2004-10-08 15:00:00.000   
3   52069      Disney  Cathartes aura  2004-10-11 14:00:00.000   
4   57954       Prado  Cathartes aura  2005-11-02 15:00:00.000   

           deploy-off-date animal-comments animal-life-stage  animal-mass  \
0  2004-03-14 20:00:01.000       migratory             adult       2372.0   
1  2013-03-18 22:00:01.000   non-migratory             adult       2012.0   
2  2006-03-29 17:00:01.000       migratory             adult       1951.0   
3  2011-10-18 23:00:01.000       migratory             adult       2108.0   
4  2009-07-07 00:00:01.000   non-migratory             adult       1710.0   

  attachment-type                                deployment-comments  \
0         harness  trapped in Pennsylvania using padded-leg hold ...   
1         harness  trapped in Pennsylvania using padded-leg hold ...   
2         harness  trapped in Pennsylvania using padded-leg hold ...   
3         harness  trapped in Pennsylvania using padded-leg hold ...   
4         harness          trapped in California using walk-in traps   

      deployment-id      duty-cycle                   study-site  \
0  42500-Butterball  1 fix per hour  East Coast of North America   
1        52067-Irma  1 fix per hour  East Coast of North America   
2  42500-Schaumboch  1 fix per hour  East Coast of North America   
3      52069-Disney  1 fix per hour  East Coast of North America   
4       57954-Prado  1 fix per hour  West Coast of North America   

  tag-manufacturer-name  tag-mass tag-model  
0   Microwave Telemetry      70.0    PTT100  
1   Microwave Telemetry      70.0    PTT100  
2   Microwave Telemetry      70.0    PTT100  
3   Microwave Telemetry      70.0    PTT100  
4   Microwave Telemetry      70.0    PTT100

In [15]:
vulture_info_df.columns

Index(['tag-id', 'animal-id', 'animal-taxon', 'deploy-on-date',
       'deploy-off-date', 'animal-comments', 'animal-life-stage',
       'animal-mass', 'attachment-type', 'deployment-comments',
       'deployment-id', 'duty-cycle', 'study-site', 'tag-manufacturer-name',
       'tag-mass', 'tag-model'],
      dtype='object')

In [16]:
# Select columns 
new_vulture_info_df = vulture_info_df[['tag-id', 'animal-id', 'animal-taxon', 'deploy-on-date',
       'deploy-off-date', 'animal-comments', 'animal-life-stage',
       'animal-mass',  'deployment-comments',
        'study-site']].copy()
new_vulture_info_df.head(1)

tag-id   animal-id    animal-taxon           deploy-on-date  \
0   42500  Butterball  Cathartes aura  2003-11-14 16:00:00.000   

           deploy-off-date animal-comments animal-life-stage  animal-mass  \
0  2004-03-14 20:00:01.000       migratory             adult       2372.0   

                                 deployment-comments  \
0  trapped in Pennsylvania using padded-leg hold ...   

                    study-site  
0  East Coast of North America

In [17]:
new_vulture_info_df.count()

tag-id                 19
animal-id              19
animal-taxon           19
deploy-on-date         19
deploy-off-date        19
animal-comments        19
animal-life-stage      19
animal-mass            12
deployment-comments    19
study-site             19
dtype: int64

In [18]:
new_vulture_info_df.to_sql(name='vulture_detail', con=engine, if_exists='append', index=False)

### Confirm data has been added by querying
* NOTE: can also check using pgAdmin

In [19]:
pd.read_sql_query('select * from migration_paths', con=engine).head()

event-id                timestamp  location-long  location-lat  \
0  283203879  2003-11-14 16:00:00.000      -75.39717      40.48933   
1  283203880  2003-11-14 17:00:00.000      -75.39717      40.48933   
2  283203881  2003-11-14 18:00:00.000      -75.33317      40.32467   
3  283203882  2003-11-14 19:00:00.000      -75.35617      40.33983   
4  283203883  2003-11-14 20:00:00.000      -75.42650      40.31550   

  individual-taxon-canonical-name  tag-local-identifier  \
0                  Cathartes aura                 42500   
1                  Cathartes aura                 42500   
2                  Cathartes aura                 42500   
3                  Cathartes aura                 42500   
4                  Cathartes aura                 42500   

  individual-local-identifier  
0                  Butterball  
1                  Butterball  
2                  Butterball  
3                  Butterball  
4                  Butterball

In [20]:
pd.read_sql_query('select * from vulture_detail', con=engine).head()

tag-id   animal-id    animal-taxon           deploy-on-date  \
0   42500  Butterball  Cathartes aura  2003-11-14 16:00:00.000   
1   52067        Irma  Cathartes aura  2004-09-06 17:00:00.000   
2   42500  Schaumboch  Cathartes aura  2004-10-08 15:00:00.000   
3   52069      Disney  Cathartes aura  2004-10-11 14:00:00.000   
4   57954       Prado  Cathartes aura  2005-11-02 15:00:00.000   

           deploy-off-date animal-comments animal-life-stage  animal-mass  \
0  2004-03-14 20:00:01.000       migratory             adult       2372.0   
1  2013-03-18 22:00:01.000   non-migratory             adult       2012.0   
2  2006-03-29 17:00:01.000       migratory             adult       1951.0   
3  2011-10-18 23:00:01.000       migratory             adult       2108.0   
4  2009-07-07 00:00:01.000   non-migratory             adult       1710.0   

                                 deployment-comments  \
0  trapped in Pennsylvania using padded-leg hold ...   
1  trapped in Pennsylvania using padded-leg hold ...   
2  trapped in Pennsylvania using padded-leg hold ...   
3  trapped in Pennsylvania using padded-leg hold ...   
4          trapped in California using walk-in traps   

                    study-site  
0  East Coast of North America  
1  East Coast of North America  
2  East Coast of North America  
3  East Coast of North America  
4  West Coast of North America

In [21]:
engine.table_names()

['migration_paths', 'vulture_detail']

In [22]:
conn = engine.connect()

from sqlalchemy.orm import Session
from sqlalchemy.ext.declarative import declarative_base
Base = declarative_base()

session = Session(bind=engine)
Base.metadata.create_all(engine)
session.commit()

In [23]:
new_vulture_data_df.head()

event-id                timestamp  location-long  location-lat  \
0  283203879  2003-11-14 16:00:00.000      -75.39717      40.48933   
1  283203880  2003-11-14 17:00:00.000      -75.39717      40.48933   
2  283203881  2003-11-14 18:00:00.000      -75.33317      40.32467   
3  283203882  2003-11-14 19:00:00.000      -75.35617      40.33983   
4  283203883  2003-11-14 20:00:00.000      -75.42650      40.31550   

  individual-taxon-canonical-name  tag-local-identifier  \
0                  Cathartes aura                 42500   
1                  Cathartes aura                 42500   
2                  Cathartes aura                 42500   
3                  Cathartes aura                 42500   
4                  Cathartes aura                 42500   

  individual-local-identifier  
0                  Butterball  
1                  Butterball  
2                  Butterball  
3                  Butterball  
4                  Butterball

In [24]:
vulture_city = new_vulture_data_df[['location-lat', 'location-long']]
vulture_city.head()

location-lat  location-long
0      40.48933      -75.39717
1      40.48933      -75.39717
2      40.32467      -75.33317
3      40.33983      -75.35617
4      40.31550      -75.42650

# list of cities

In [25]:
lats = new_vulture_data_df['location-lat'].values.tolist()
lngs = new_vulture_data_df['location-long'].values.tolist()
type(lngs)

list

In [26]:
lat_lngs = []
cities = []
lat_lngs = zip(lats, lngs)

In [27]:
for lat_lng in lat_lngs:
    target_lat = lat_lng[0]
    target_lng = lat_lng[1]
    
    print(target_lat, target_lng)

40.48933 -75.39717
40.48933 -75.39717
40.32467 -75.33317
40.33983 -75.35617
40.3155 -75.4265
40.30383 -75.405
40.29567 -75.41133
40.29567 -75.41167
40.296 -75.41183
40.29583 -75.41167
40.29583 -75.41167
40.29583 -75.41167
40.29567 -75.41167
40.26183 -75.39233
40.25617 -75.397
40.25617 -75.397
40.22433 -75.365
40.02283 -75.35233
40.02067 -75.354
40.02067 -75.35417
40.01333 -75.35533
40.01267 -75.35567
40.0125 -75.35583
39.681 -75.88867
39.55483 -76.00667
39.55483 -76.00683
39.5545 -76.00667
39.55483 -76.00683
39.55467 -76.00683
39.55467 -76.00717
39.5585 -76.01617
39.55783 -76.0245
39.563 -76.0155
39.56317 -76.01417
39.56317 -76.01417
39.5545 -76.00683
39.5545 -76.00683
39.55467 -76.00667
39.55467 -76.00683
39.55467 -76.00683
39.55483 -76.00417
39.55467 -76.0045
39.55467 -76.0045
39.57183 -76.058
39.52233 -76.258
39.423 -76.45933
39.40933 -76.65717
39.39467 -76.72383
39.399 -76.71433
39.39683 -76.70767
39.39717 -76.708
39.39667 -76.70817
39.39683 -76.708
39.39717 -76.708
39.3975 -76.706

28.77067 -80.94717
28.77033 -80.94717
28.77033 -80.94717
28.77033 -80.94717
28.7705 -80.94717
28.77033 -80.94717
28.77033 -80.94717
28.7705 -80.9475
28.77033 -80.94717
28.7705 -80.94733
28.61217 -80.87767
28.612 -80.87767
28.61217 -80.87767
28.612 -80.8775
28.61183 -80.8775
28.612 -80.8775
28.61217 -80.87783
28.61183 -80.87767
28.61183 -80.8775
28.61183 -80.87767
28.612 -80.87767
28.612 -80.878
28.612 -80.87783
28.612 -80.87783
28.57183 -81.03083
28.53583 -81.20817
28.5895 -81.2415
28.63567 -81.19133
28.658 -81.06717
28.7045 -81.14333
28.70433 -81.12317
28.70467 -81.12133
28.70517 -81.12167
28.70517 -81.1215
28.705 -81.12167
28.70517 -81.122
28.70483 -81.12133
28.704 -81.121
28.70567 -81.12183
28.70567 -81.12167
28.79767 -81.07333
28.8155 -81.14467
28.89767 -81.31017
29.00467 -81.27083
29.00617 -81.32
29.00833 -81.32267
29.00833 -81.32283
29.00833 -81.32267
29.0085 -81.32283
29.00833 -81.32267
29.00833 -81.32267
29.0065 -81.31933
29.00667 -81.3195
29.00767 -81.3175
29.01133 -81.3115
29

27.76383 -80.608
27.76383 -80.608
27.7655 -80.60317
29.07517 -81.21067
29.075 -81.21067
29.07433 -81.20967
29.0745 -81.20967
29.07433 -81.20983
29.07433 -81.20967
29.07533 -81.20933
29.07467 -81.20967
29.58883 -81.26783
29.589 -81.2675
29.5865 -81.26517
29.58617 -81.265
29.57817 -81.26067
29.57183 -81.25367
29.57183 -81.25367
29.572 -81.25367
29.57183 -81.25383
31.56867 -81.60533
31.56867 -81.6055
31.63117 -81.5625
32.61267 -80.91767
32.61233 -80.91767
32.6125 -80.91833
32.61233 -80.91783
32.61233 -80.91783
32.61217 -80.91767
32.61233 -80.91783
32.61217 -80.91783
32.61217 -80.91783
32.61233 -80.91767
32.66867 -80.85817
32.99333 -80.528
33.395 -80.26533
33.76117 -80.03817
34.17083 -79.68933
34.52633 -79.1745
34.85517 -78.643
34.8555 -78.64367
34.85517 -78.64083
34.855 -78.64083
34.855 -78.64083
34.85517 -78.641
34.85483 -78.64217
34.85567 -78.6435
34.85567 -78.64383
34.85567 -78.64367
34.914 -78.5195
35.40667 -77.3715
35.40667 -77.37133
35.40683 -77.3715
35.40783 -77.37083
35.4095 -77.3

25.662 -81.26283
25.662 -81.26267
25.662 -81.26267
25.662 -81.26267
25.73967 -81.344
26.00517 -81.40883
26.19667 -81.56733
26.1795 -81.671
26.1625 -81.6605
26.2775 -81.72433
26.29917 -81.67817
26.29833 -81.678
26.2975 -81.67917
26.29867 -81.677
26.29917 -81.6785
26.29917 -81.6785
26.299 -81.6785
26.29917 -81.67883
26.29833 -81.67917
26.28667 -81.669
26.24317 -81.681
26.1855 -81.66883
26.1925 -81.6645
26.26783 -81.62983
26.2685 -81.63117
26.267 -81.63467
26.26667 -81.63483
26.26667 -81.63733
26.26667 -81.63733
26.26667 -81.63733
26.2665 -81.63733
26.26667 -81.63517
26.26783 -81.634
26.4575 -81.812
26.6725 -81.8885
26.79333 -81.9655
26.79283 -81.96083
26.73433 -81.99517
26.65483 -81.993
26.655 -81.994
27.233 -82.05567
27.233 -82.0555
27.233 -82.05567
27.23283 -82.0555
27.23283 -82.05533
27.23283 -82.05533
27.23267 -82.058
27.23383 -82.06183
27.23367 -82.06183
27.236 -82.06367
27.23383 -82.062
27.23217 -82.05733
27.23217 -82.05733
27.23283 -82.05567
27.23283 -82.05567
27.233 -82.05583
27.

27.40333 -80.401
27.40117 -80.40167
27.40117 -80.40167
27.40217 -80.40133
27.40217 -80.40133
27.385 -80.39167
27.3855 -80.39233
27.40717 -80.38433
27.44567 -80.29483
27.44283 -80.296
27.44283 -80.29633
27.44267 -80.29633
27.38633 -80.39217
27.391 -80.39083
27.38783 -80.393
27.40333 -80.40067
27.4035 -80.3995
27.4035 -80.39917
27.40367 -80.399
27.40217 -80.4015
27.40217 -80.401
27.40333 -80.40083
27.40333 -80.39933
27.40383 -80.3995
27.403 -80.40133
27.403 -80.4015
27.403 -80.40133
27.403 -80.40133
27.4025 -80.401
27.4025 -80.40117
27.40217 -80.40083
27.4075 -80.4035
27.40217 -80.40133
27.4035 -80.4005
27.40333 -80.40067
27.4035 -80.40067
27.40317 -80.4005
27.40333 -80.4005
27.40117 -80.4
27.40133 -80.4005
27.38133 -80.39817
27.38133 -80.399
27.38133 -80.4
27.3765 -80.40133
27.387 -80.3925
27.386 -80.39183
27.392 -80.39317
27.4035 -80.40067
27.40217 -80.4
27.40183 -80.39833
27.40183 -80.39833
27.40167 -80.39833
27.40133 -80.4025
27.40333 -80.39967
27.4035 -80.39967
27.40317 -80.4035
27.

...

40.9969 -75.8369
40.9912 -75.8121
40.9426 -75.8307
40.9426 -75.8306
40.9427 -75.8306
40.9425 -75.8307
40.9427 -75.8307
40.9382 -75.8226
41.0287 -75.8062
41.0162 -75.7664
41.0239 -75.7744
41.024 -75.7746
41.0237 -75.7745
41.0245 -75.7743
41.0239 -75.7744
41.0162 -75.8455
41.0103 -76.1188
41.0159 -76.0984
41.0111 -76.11
41.0112 -76.11
41.0112 -76.1101
41.0111 -76.1101
41.0112 -76.11
41.0112 -76.1101
41.018 -76.1504
41.0113 -76.1449
41.0106 -76.1439
41.0113 -76.1448
41.0113 -76.1449
41.0114 -76.1448
41.0152 -76.1417
41.0154 -76.081
41.0153 -76.0802
41.0144 -76.0804
41.0144 -76.0804
41.0145 -76.0807
41.0144 -76.0804
41.0144 -76.0804
41.0144 -76.0804
41.0044 -76.0721
41.0346 -75.8646
41.0333 -75.8591
41.0334 -75.8591
41.0335 -75.8592
41.0334 -75.8593
41.0334 -75.8592
41.0334 -75.8575
41.0269 -75.8532
40.9995 -76.0801
40.9999 -76.079
40.9999 -76.0789
40.9999 -76.079
40.9998 -76.0789
40.9995 -76.0801
41.0 -76.0782
41.0263 -76.0676
41.0528 -76.0895
41.0926 -76.0182
41.0933 -76.0184
41.0935 -76

40.7896 -76.2836
40.6513 -76.601
40.7955 -76.2486
40.7965 -76.265
40.7897 -76.2835
40.7894 -76.2833
40.7898 -76.2837
40.7896 -76.2837
40.7897 -76.2835
40.7992 -76.2714
40.8948 -76.4114
40.8941 -76.4124
40.8948 -76.4112
40.8948 -76.4113
40.8948 -76.4113
40.8948 -76.4113
40.8373 -76.2672
40.7902 -76.2422
40.7901 -76.2475
40.7896 -76.2835
40.7896 -76.2838
40.7896 -76.2837
40.7999 -76.2714
40.7951 -76.2655
40.797 -76.2478
40.893 -76.5536
40.921 -76.538
40.7896 -76.2836
40.7896 -76.2837
40.7896 -76.2837
40.7895 -76.2835
40.8001 -76.2712
40.7998 -76.2714
40.7999 -76.2713
40.8002 -76.271
40.7896 -76.2836
40.7896 -76.2837
40.8027 -76.2213
40.8015 -76.2636
40.961 -76.4824
40.9555 -76.4569
40.9556 -76.457
40.9557 -76.457
40.9556 -76.457
40.9556 -76.457
40.9232 -76.4897
40.8062 -76.7089
40.7919 -76.2402
40.7896 -76.2834
40.7897 -76.2837
40.7897 -76.2837
40.7895 -76.2835
40.7998 -76.2715
40.8025 -76.219
40.8115 -76.2418
40.8743 -76.5526
40.7896 -76.2836
40.7895 -76.2836
40.7895 -76.2835
40.7896 -7

40.8012 -76.2257
40.8095 -76.2398
40.8095 -76.24
40.8096 -76.24
40.8096 -76.2401
40.8095 -76.2399
40.8096 -76.2399
40.8095 -76.2399
40.7621 -76.2292
40.7635 -76.2328
40.8112 -76.2492
40.7935 -76.2302
40.8101 -76.2402
40.8095 -76.2399
40.8095 -76.2399
40.8095 -76.2398
40.7969 -76.2702
40.7995 -76.221
40.7911 -76.28
40.7898 -76.284
40.7897 -76.2842
40.79 -76.2841
40.7898 -76.284
40.7994 -76.2717
40.8002 -76.271
40.8156 -76.2526
40.7908 -76.2825
40.7896 -76.2835
40.7896 -76.2836
40.7895 -76.2837
40.7999 -76.2714
40.8161 -76.2417
40.8229 -76.2433
40.7899 -76.2839
40.7898 -76.284
40.7899 -76.284
40.7894 -76.2838
40.7897 -76.2841
40.7899 -76.284
40.7979 -76.2748
40.8134 -76.2559
40.7897 -76.2835
40.7898 -76.284
40.79 -76.2841
40.79 -76.284
40.7897 -76.284
40.7952 -76.2851
40.7999 -76.2714
40.8008 -76.2366
40.8097 -76.2606
40.7896 -76.2836
40.7895 -76.2836
40.7897 -76.2836
40.7896 -76.2837
40.8 -76.2713
40.7999 -76.2714
40.7958 -76.2796
40.8266 -76.6186
40.8282 -76.6022
40.8734 -76.6932
40.78

40.7961 -76.2797
40.7957 -76.2797
40.7957 -76.2797
40.8021 -76.2352
40.8086 -76.2384
40.7955 -76.2556
40.8054 -76.2317
40.796 -76.2795
40.7958 -76.2795
40.7958 -76.2795
40.7959 -76.2796
40.7998 -76.2699
40.7922 -76.2478
40.8113 -76.2265
40.8096 -76.221
40.7956 -76.2795
40.7957 -76.2797
40.7958 -76.2797
40.7958 -76.2797
40.7997 -76.27
40.8223 -76.2166
40.8 -76.2715
40.7959 -76.2801
40.7957 -76.2799
40.7958 -76.2799
40.7958 -76.2797
40.8057 -76.243
40.8082 -76.2261
40.8065 -76.2176
40.8188 -76.2322
40.7957 -76.2797
40.7958 -76.2795
40.7957 -76.2797
40.7958 -76.2797
40.7956 -76.2794
40.8056 -76.2202
40.8142 -76.2262
40.803 -76.2168
40.796 -76.2799
40.7958 -76.2797
40.7957 -76.2796
40.7957 -76.2796
40.8001 -76.2709
40.8 -76.2711
40.8081 -76.2425
40.7919 -76.2564
40.7961 -76.2797
40.7963 -76.2798
40.7958 -76.2797
40.7963 -76.2799
40.8032 -76.216
40.8212 -76.2271
40.8073 -76.2326
40.7958 -76.2804
40.7959 -76.2792
40.7957 -76.2797
40.8188 -76.2245
40.8192 -76.2244
40.8061 -76.2316
40.8138 -76

40.7898 -76.2841
40.7898 -76.284
40.7899 -76.284
40.7896 -76.2402
40.8196 -76.2437
40.8196 -76.2437
40.7898 -76.2841
40.7899 -76.2841
40.7899 -76.284
40.7899 -76.284
40.7899 -76.2841
40.7951 -76.2753
40.795 -76.2753
40.795 -76.2753
40.7949 -76.2757
40.7948 -76.2788
40.7948 -76.2788
40.7948 -76.2789
40.7957 -76.2798
40.7979 -76.2748
40.8747 -76.2472
40.8998 -76.2024
40.9106 -76.2096
40.9091 -76.2129
40.9091 -76.2128
40.9091 -76.2129
40.9109 -76.2107
40.9039 -76.1973
40.792 -76.2234
40.8196 -76.2438
40.8213 -76.2428
40.8213 -76.2428
40.8214 -76.2428
40.8212 -76.2429
40.8215 -76.2424
40.8158 -76.241
40.8771 -76.3107
40.7721 -76.3685
40.7877 -76.2824
40.7904 -76.2893
40.7898 -76.2841
40.7898 -76.2841
40.7998 -76.2714
40.7908 -76.2247
40.8681 -76.2602
40.8299 -76.2742
40.8304 -76.2661
40.8302 -76.2662
40.8302 -76.2661
40.8303 -76.2664
40.8303 -76.2664
40.7912 -76.2342
40.7778 -76.2499
40.8092 -76.2305
40.7897 -76.284
40.79 -76.2841
40.7898 -76.2842
40.7898 -76.284
40.7899 -76.284
40.7975 -7

In [28]:
base_url = ('https://maps.googleapis.com/maps/api/geocode/json?'
    'latlng={0},{1}&key={2}').format(target_lat, target_lng, gkey)

In [29]:
geo_data = requests.get(base_url).json()

In [30]:
res = geo_data["results"]
res

[{'address_components': [{'long_name': '2604',
    'short_name': '2604',
    'types': ['street_number']},
   {'long_name': 'Water Street', 'short_name': 'Water St', 'types': ['route']},
   {'long_name': 'Mahanoy Plane',
    'short_name': 'Mahanoy Plane',
    'types': ['neighborhood', 'political']},
   {'long_name': 'Gilberton',
    'short_name': 'Gilberton',
    'types': ['locality', 'political']},
   {'long_name': 'Schuylkill County',
    'short_name': 'Schuylkill County',
    'types': ['administrative_area_level_2', 'political']},
   {'long_name': 'Pennsylvania',
    'short_name': 'PA',
    'types': ['administrative_area_level_1', 'political']},
   {'long_name': 'United States',
    'short_name': 'US',
    'types': ['country', 'political']},
   {'long_name': '17934', 'short_name': '17934', 'types': ['postal_code']}],
  'formatted_address': '2604 Water St, Gilberton, PA 17934, USA',
  'geometry': {'location': {'lat': 40.7930689, 'lng': -76.2452732},
   'location_type': 'ROOFTOP',
   '

In [31]:
# Identify nearest city for each lat, lng combination
for lat_lng in lat_lngs:
    city = citipy.nearest_city(lat_lng[0], lat_lng[1]).city_name
    cities.append(city)